# Inversion d'une matrice triangulaire inférieure

Marc Lorenzi

1er février 2021

In [ ]:
import matplotlib.pyplot as plt
from fractions import Fraction
import random
import time

## 1. Préliminaires 

### 1.1 Qu'allons-nous faire ?

On note $\mathcal T_n(\mathbb R)$ l'ensemble des matrices $n\times n$ triangulaires **inférieures**.

Nous allons dans ce notebook nous intéresser aux deux problèmes suivants. Soit $A\in\mathcal T_n(\mathbb R)$ une matrice inversible (l'inversibilité de $A$ est équivalente à la non nullité de ses coefficients diagonaux).

- Problème 1 : Étant donné $Y\in\mathcal M_{n1}(\mathbb R)$, résoudre le système $AX=Y$, d'inconnue $X\in\mathcal M_{n1}(\mathbb R)$.
- Problème 2 : Inverser la matrice $A$.

Nous allons en fait voir que si l'on sait résoudre le premier problème on sait aussi résoudre le second, *à condition d'anticiper un peu les choses*.

### 1.2 Opérations sur les listes

La fonction `sub` prend en paramètres deux listes de nombres $X$ et $Y$ et renvoie $X-Y$.

In [ ]:
def sub(X, Y):
    n = len(X)
    Z = n * [None]
    for i in range(n):
        Z[i] = X[i] - Y[i]
    return Z

In [ ]:
sub([1, 2, 3, 4], [5, 4, 3, 2])

La fonction `mult` prend en paramètres un nombre $t$ et une liste $X$ et renvoie la liste $tX$.

In [ ]:
def mult(t, X):
    n = len(X)
    Y = n * [None]
    for i in range(n):
        Y[i] = t * X[i]
    return Y

In [ ]:
mult(3, [1, 2, 3, 4])

### 1.3 Matrices triangulaires aléatoires

La fonction `random_triang` prend un entier $n$ en paramètre. Elle renvoie une matrice triangulaire inférieure inversible « aléatoire » de taille $n$.

In [ ]:
def random_triang(n, M=1000):
    A = n * [None]
    for i in range(n):
        A[i] = n * [0]
        A[i][i] = random.randint(1, M)
        r = random.randint(0, 1)
        if r == 0: A[i][i] = - A[i][i]
        for j in range(i):
            A[i][j] = random.randint(-M, M)
    return A

In [ ]:
print(random_triang(10))

Clairement, nous allons avoir du mal à lire des matrices affichées de la sorte. Écrivons donc une fonction qui affiche joliment une matrice.

In [ ]:
def print_joli(A):
    m = len(A)
    n = len(A[0])
    w = n * [0]
    for i in range(m):
        for j in range(n):
            w[j] = max(w[j], len(str(A[i][j])))
    fmt = ''
    for j in range(n):
        fmt += '%' + str(w[j] + 2) + 's'
    for i in range(m):
        print(fmt % tuple(A[i]))

In [ ]:
print_joli(random_triang(10))

C'est beaucoup mieux.

## 2. Résolution d'un système triangulaire

### 2.1 Un peu de théorie

Soit $A\in\mathcal T_n(\mathbb R)$ une matrice triangulaire inférieure de taille $n$. Supposons que $A$ est inversible.

Soit $Y=(y_1\ y_2\ \ldots\ y_n)^T\in\mathcal M_{n1}(\mathbb R)$. Quelle est l'unique solution du système $AX=Y$, d'inconnue $X=(x_1\ x_2\ \ldots\ x_n)^T\in\mathcal M_{n1}(\mathbb R)$ ? Ce système est, si l'on développe le tout,

$$\left\lbrace\begin{array}{llllllll}
A_{11}x_1&&&&&&&=&y_1\\
A_{21}x_1&+&A_{22}x_2&&&&&=&y_2\\
&&&\ldots\\
A_{n1}x_1&+&A_{n2}x_2&+&\ldots&+&A_{nn}x_n&=&y_n\\
\end{array}\right.$$

On a $A_{11}x_1=y_1$ d'où, immédiatement,

$$x_1=\frac 1 {A_{11}}y_1$$

Soit $i\in[|1,n|]$. Supposons trouvés $x_{1},\ldots,x_{i-1}$. La $i$ème ligne du système $AX=Y$ est

$$\sum_{j=1}^iA_{ij}x_j=y_i$$

On en tire immédiatement

$$x_i=\frac 1 {A_{ii}}\left(y_i-\sum_{j=1}^{i-1}A_{ij}x_j\right)$$

### 2.2 La fonction Python

Écrire une fonction résolvant le système $AX=Y$ est donc plus ou moins immédiat. Une simple boucle `for` suffit, en faisant simplement attention à une chose : comme nous manipulons des listes Python, les indices vont de $0$ à $n-1$ et pas de $1$ à $n$.

On se contente dans la fonction `resoudre_triang` ci-dessous d'appliquer la formule trouvée dans le paragraphe précédent.

**Remarque.** Lorsque le paramètre optionnel `exact` vaut `True`, les calculs sont fait de façon exacte (lorsque la matrice $A$ est à coefficients entiers ou rationnels). Lorsque ce paramètre vaut `False`,  les calculs sont fait en utilisant des `float`. Les calculs exacts sont très coûteux car les dénominateurs des fractions ont tendance à devenir énormes lorsque la taille de la matrice augmente.

In [ ]:
def resoudre_triang(A, Y, exact=True):
    n = len(A)
    X = n * [None]
    for i in range(n):
        X[i] = Y[i]
        for j in range(i):
            X[i] = sub(X[i], mult(A[i][j], X[j]))
        if exact: X[i] = mult(Fraction(1, A[i][i]), X[i])
        else: X[i] = mult(1 / A[i][i], X[i])
    return X        

Testons avec une matrice $4\times 4$ et un second membre $Y$ tel que la solution du système soit $(1\ 2\ 3\ 4)^T$. Il suffit évidemment de prendre $Y=A(1\ 2\ 3\ 4)^T$.

In [ ]:
A = [[1, 0, 0, 0],
    [2, 1, 0, 0],
    [3, 4, 1, 0],
    [5, 6, 7, 1]]

Y = [[1], [4], [14], [42]]
X = resoudre_triang(A, Y)
print_joli(X)

### 2.3 Complexité

Quel est le nombre d'opérations nécessaire à la résolution d'un système triangulaire ? Notons $C(n)$ cette quantité, qui dépend seulement de la taille du système à résoudre.

La fonction `resoudre_triang` effectue une boucle `for` sur l'entier $i$. Cette boucle est exécutée $n$ fois. À la $i$ème itération, la boucle sur $j$ est effectuée $i$ fois. À chaque itération de la boucle sur $j$, on effectue 2 opérations (une soustraction et une multiplication). Enfin, à chaque itération de la boucle sur $i$, on effectue une division. Ainsi, chaque itération de la boucle sur $i$ nécessite $2i+1$ opérations. Finalement,

$$C(n)=\sum_{i=0}^{n-1}(2i+1)=n+2\sum_{i=0}^{n-1} i$$

La somme $\sum_{i=0}^{n-1} i$ vaut $\frac 1 2 n (n-1)$. On en déduit

$$C(n)=n+n(n-1)= n^2$$

**La résolution d'un système triangulaire de taille $n$ nécessite $n^2$ opérations.**

## 3. Inverser une matrice triangulaire

### 3.1 Se ramener à ce qui précède

Trouver l'inverse de la matrice $A$ c'est aussi résoudre un système, le système $AX=Y$ où $Y=I_n$ est la matrice identité d'ordre $n$ et l'inconnue $X$ est une matrice $n\times n$. Il s'avère que les formules que nous avons obtenues au paragraphe 2.2 sont toujours valides, en interprétant $x_i$ et $y_i$ non plus comme des nombres mais comme comme la $i$ème ligne de la matrice $X$ et de la matrice $Y$, c'est à dire des listes.

Mais alors, se pourrait-il que notre fonction `resoudre_triang` puisse aussi inverser les matrices ? On peut toujours rêver ... et pour une fois le rêve devient réalité 😀. En fait il n'y a rien à écrire, ça marche tout seul ou presque.

### 3.2 La fonction Python

Écrivons juste une fonction `eye` qui renvoie la matrice identité d'ordre $n$.

In [ ]:
def eye(n):
    E = n * [None]
    for i in range(n):
        E[i] = n * [0]
        E[i][i] = 1
    return E

In [ ]:
print_joli(eye(5))

La fonction `inverse_triang` renvoie l'inverse de la matrice triangulaire $A$. Cett fonction appelle `resoudre_triang`  avec un second membre du système égal à $I_n$.

In [ ]:
def inverse_triang(A, exact=True):
    n = len(A)
    return resoudre_triang(A, eye(n), exact)

In [ ]:
A = [[1, 0, 0, 0],
    [2, 1, 0, 0],
    [3, 4, 1, 0],
    [5, 6, 7, 1]]

print_joli(inverse_triang(A))

Tests sur une matrice aléatoire ...

In [ ]:
A = random_triang(5, M=100)
print_joli(A)
print_joli(inverse_triang(A))

**Exercice.** Exécutez plusieurs fois la cellule ci-dessus. Que remarquez-vous à propos des coefficients diagonaux de l'inverse de $A$ ? Pouvez-vous le prouver ?

### 3.3 Vérifications

Nous sommes confiants dans notre fonction d'inversion de matrices, mais deux précautions valent mieux qu'une. La fonction `prodmat` renvoie le produit $AB$ de deux matrices $A$ et $B$. Elle prend en paramètres une matrice $A\in\mathcal M_{pq}(\mathbb R)$ et une matrice $B\in\mathcal M_{qr}(\mathbb R)$. Elle renvoie la matrice $C\in\mathcal M_{pr}(\mathbb R)$ définie pour $i\in[|0,p-1|]$ et $j\in[|0,r-1|]$ par

$$C_{ij}=\sum_{k=0}^{q-1}A_{ik}B_{kj}$$

In [ ]:
def prodmat(A, B):
    p = len(A)
    q = len(B)
    r = len(B[0])
    C = p * [None]
    for i in range(p): C[i] = r * [0]
    for i in range(p):
        for k in range(q):
            for j in range(r):
                C[i][j] = C[i][j] + A[i][k] * B[k][j]
    return C

Prenons une matrice $A$, calculons son inverse $A'$, puis affichons le produit $AA'$. La cellule ci-dessous devrait tout le temps afficher la matrice identité.

In [ ]:
A = random_triang(10, 1000)
#print_joli(A)
A1 = inverse_triang(A)
print_joli(prodmat(A, A1))

### 3.4 Temps de calcul

La résolution d'un système triangulaire nécessite $n^2$ opérations. Inverser une matrice triangulaire nécessite toujours $n^2$ opérations, mais ces opérations se font sur des listes de taille $n$. Chacune de ces opérations nécessite ainsi $n$ opérations sur des nombres, ce qui donne au total $n^3$ opérations pour l'obtention de l'inverse. Illustrons cela par un dessin.

La fonction `temps_calcul` renvoie le temps mis pour inverser une matrice de taille $n$. Le calcul est fait en virgule flottante, sinon les temps deviennent très vite prohibitifs.

In [ ]:
def temps_calcul(n):
    A = random_triang(n)
    t1 = time.time()
    A1 = inverse_triang(A, False)
    t2 = time.time()
    return t2 - t1

Combien de temps faut-il pour inverser une matrice de taille 100 ? 

In [ ]:
t100 = temps_calcul(100)
print(t100)

Si nous appelons $T_n$ le temps nécessaire à l'inversion d'une matrice de taille $n$, nous devrions avoir

$$T_n\simeq Cn^3$$

où $C$ est une constante. Pourquoi « à peu près égal » ? Tout simplement parce que le temps de calcul ne dépend pas **que** des opérations arithmétiques effectuées. Il y a aussi dans nos fonctions des créations de listes, des accès à des éléments de listes, des modifications d'éléments de listes, etc.

Que vaut $C$ ? Cette constante dépend évidemment de la machine utilisée, et nous pouvons facilement en obtenir la valeur :

In [ ]:
C = t100 / 100 ** 3
print(C)

La fonction `plot_temps` affiche :

- En noir, les temps de calcul pour des matrices de taille $n=$ 10, 20, 30, ..., $N$.
- En rouge, les temps « théoriques » $Cn^3$.

In [ ]:
def plot_temps(N):
    temps = []
    ns = range(10, N + 1, 10)
    for n in ns:
        temps.append(temps_calcul(n))
    plt.plot(ns, temps, 'k')
    cs = [C * n ** 3 for n in ns]
    plt.plot(ns, cs, 'r')
    plt.xlim(10, N)
    plt.grid()

In [ ]:
plt.rcParams['figure.figsize'] = (10, 6)

In [ ]:
plot_temps(150)

La concordance entre les deux courbes n'est pas trop mauvaise ...

**Remarque finale.** On trouve par ci par là des gens affirmant pouvoir inverser une matrice triangulaire de taille $n$ en  $O(n^2)$ opérations. Supposons que ce soit le cas. Soient $A$ et $B$ deux matrices $n\times n$. On a le produit pas blocs suivant (matrices de taille $3n\times 3n$) :

$$\begin{pmatrix}I_n&0&0\\B&I_n&0\\0&A&I_n\end{pmatrix}\begin{pmatrix}I_n&0&0\\-B&I_n&0\\AB&-A&I_n\end{pmatrix}=I_{3n}$$

Ces deux matrices sont triangulaires. L'inverse de la première matrice est la seconde matrice, et on peut lire en haut à droite de la seconde matrice le produit $AB$. Ainsi, si on savait inverser une matrice triangulaire  de taille $n$ en $O(n^2)$ opérations, on saurait multiplier deux matrices $n\times n$ quelconques en $O(n^2)$ opérations. Remarquons que $n^2$ est le nombre de coefficients de ces matrices !

Il existe une réciproque à ce que nous venons de dire : si on sait multiplier deux matrices $n\times n$ en temps $O(n^\omega)$ (où $\omega\ge 2$), alors on sait aussi inverser une matrice $n\times n$ quelconque en temps $O(n^\omega)$. Ne cherchez pas pourquoi, ce n'est pas trivial du tout.

Le « record actuel » (à ma connaissance) pour la complexité du produit de deux matrices $n\times n$ (et donc pour l'inversion des matrices) est $O(n^{2.3728639})$ (Le Gall, 2014).

## 4. Mini projet

Vous pensez avoir tout compris ? Faites une copie de ce notebook. Modifiez la copie pour résoudre les deux problèmes (résolution de systèmes, inversion) pour les matrices triangulaires **supérieures**.